In [4]:
import json

with open('db.json', 'r') as f:
    # Load the JSON data from the file
    # This will raise an error if the file is not valid JSON
    data = json.load(f)


In [44]:
import json
import re

def extract_english_lesson_text(data: dict) -> str:
    """
    Build a clean English lesson string.

    • Sentences inside each paragraph run together on one line,
      separated by a single space.
    • Paragraphs are separated by one blank line ('\\n\\n').
    • No leading/trailing blank lines or double‑spaces remain.
    """
    paragraphs = []

    # walk through paragraphs in numeric order
    for para in sorted(data["page"]["paragraphs"].values(),
                       key=lambda p: p["nr"]):

        # collect lines in order and join them with a space
        raw_para = " ".join(
            line["content"].strip()
            for line in sorted(para["lines"].values(), key=lambda l: l["nr"])
        )

        # collapse any accidental runs of whitespace
        clean_para = re.sub(r"\s+", " ", raw_para).strip()
        paragraphs.append(clean_para)

    return "\n\n".join(paragraphs)


# ---- example usage ----
#
# with open("lesson20.json", encoding="utf-8") as f:
#     lesson_json = json.load(f)
# text = extract_english_lesson_text(lesson_json)
# print(text)


In [45]:
import json
import re

def extract_farsi_lesson_text(data: dict) -> str:
    """
    Return the Persian translation of the lesson.

    • All lines inside a paragraph are joined with one space.
    • Paragraphs are separated by a single blank line ('\\n\\n').
    """
    paragraphs = []

    # Iterate over paragraph objects in numeric order
    for para in sorted(data["page"]["paragraphs"].values(),
                       key=lambda p: p["nr"]):

        # Collect each line’s translation.content in order
        lines = [
            line["translation"]["content"].strip()
            for line in sorted(para["lines"].values(), key=lambda l: l["nr"])
            # occasionally a line might lack a translation—skip those gracefully
            if line.get("translation") and line["translation"].get("content")
        ]

        # Join lines with spaces, then normalise whitespace runs
        raw_para = " ".join(lines)
        clean_para = re.sub(r"\s+", " ", raw_para).strip()
        paragraphs.append(clean_para)

    return "\n\n".join(paragraphs)


# -------- example usage --------
#
# with open("lesson20.json", encoding="utf-8") as f:
#     lesson_json = json.load(f)
#
# farsi_text = extract_farsi_lesson_text(lesson_json)
# print(farsi_text)


In [9]:
# write output_data to file
with open('newDB.json', 'w') as f:
    json.dump(output_data, f, indent=4)

In [12]:
myMap = {}
for item in data:
    if(len(item['text']) > 0):
        myMap[item['text'][-1]] = item["video"]


In [14]:
for day_entries in output_data.values():
    for entry in day_entries:
        text_url = entry["text"]
        entry["videoAddress"] = myMap.get(text_url, "")

In [32]:
# utf-8
with open('newDB.json', 'w', encoding='utf-8') as f:
    json.dump(output_data, f, indent=4, ensure_ascii=False)


In [20]:
import requests

In [31]:
for day_entries in output_data.values():
    for entry in day_entries:
        textAddress = entry["textAddress"]
        # take the last part starting from /workbook
        uri = textAddress[textAddress.rfind("/workbook"):]
        url = "https://acim-farsi.org/api/page/current?path=" + uri
        # get the data
        response = requests.get(url)
        if response.status_code == 200:
            data = response.json()
            entry["title"] = data["page"]["title"]["fa"]
            audioUrl = data["page"]["audioUrl"]
            entry["audioAddress"] = "https://acim-farsi.org" + audioUrl if len(audioUrl) > 0 else ""
            paragraphsObj =  data["page"]["paragraphs"]
            # loop on paragraphsObj.values()
            for paragraph in paragraphsObj.values():
                paragraphText = ""
                lines = paragraph["lines"]
                for line in lines.values():
                    paragraphText += line["translation"]["content"] + " "
                entry["text"] += paragraphText + "\n"
        else:
            print(f"Failed to retrieve data from {url}")


In [1]:
import json
# open the file in write mode with utf-8 encoding and write the output_data
with open('newDB.json', 'r', encoding='utf-8') as f:
    output_data = json.load(f)

In [4]:
import os
from openai import OpenAI

client = OpenAI(
    # This is the default and can be omitted
    api_key=os.environ.get("OPENAI_API_KEY"),
)

In [3]:
import time


In [4]:
import re

In [ ]:
def extract_json_from_text(text):
        """Extracts the first valid JSON object from the text."""
        try:
            match = re.search(r'{.*}', text, re.DOTALL)
            if match:
                json_str = match.group(0)
                json_str = json_str.replace("“", '"').replace("”", '"').replace("‘", "'").replace("’", "'")
                return json.loads(json_str)
        except json.JSONDecodeError:
            return None
        return None

def extractRepetionIntervalAndAffirmationText(text, max_retries=10, delay=2):
    attempts = 0
    while attempts < max_retries:
        completion = client.chat.completions.create(
            model="gpt-4o",
            messages=[
                {"role": "system", "content": """I am going to give you persian translation of an ACIM work book lessons. you should give me repetition interval and lesson affirmation text (for short practice and longer practices) extracted from text:
        the repetition interval should be selected based on following list:
        [
        8_mintes,
        10_minutes,
        12_minutes,
        15_minutes,
        30_minutes,
        45_minutes,
        every_hour,
        every_2_hours,
        every_3_hours,
        every_4_hours,
        every_5_hours,
        every_6_hours,
        2_times,
        3_times,
        4_times,
        5_times,
        6_times,
        none
        ]
                
        The output must be a valid JSON, no explanation, no extra text. Format:
{
  "repetition Interval": "...",
  "short affirmation text": "...",
  "long affirmation text": "..."
}
        """},
                {
                    "role": "user",
                    "content": text,
                },
            ],
        )

        result = completion.choices[0].message.content
        parsed = extract_json_from_text(result)
        if parsed:
            return parsed
    
        print("Failed to decode JSON")
        print(result)
        attempts += 1
        time.sleep(delay)
    return {"error": "Failed to decode JSON after multiple attempts"}


In [8]:
import tqdm

In [ ]:
for day_entries in tqdm.tqdm(output_data.values()):
    for entry in day_entries:
        text = entry["text"]
        result = extractRepetionIntervalAndAffirmationText(text)
        entry["repetitionCode"] = result["repetition Interval"]
        entry["repetitionTextShort"] = result["short reminder text"]
        entry["repetitionTextLong"] = result["long reminder text"]

    # save to file as you are processing to update the  newDB.json file with latest content of output_data
    with open("newDB.json", "w", encoding="utf-8") as f:
        json.dump(output_data, f, ensure_ascii=False, indent=4)


  0%|          | 0/366 [00:00<?, ?it/s]

 64%|██████▍   | 235/366 [8:33:44<4:46:23, 131.17s/it]   


KeyboardInterrupt: 

In [2]:
import json

In [6]:
with open('newDB.json', 'r', encoding='utf-8') as f:
    original_data = json.load(f)

en_fa_data = {}
for day, entries in original_data.items():
    en_fa_data[day] = []
    for entry in entries:
        en_fa_entry = {}
        for key, value in entry.items():
            en_fa_entry[key] = {
                "en": '',
                "fa": value
            }
        en_fa_data[day].append(en_fa_entry)

In [7]:
en_fa_data["0"]


[{'text': {'en': '',
   'fa': 'بنیانی نظری مانند آنچه که این متن [متنِ دوره\u200cای در معجزات] ایجاد می\u200cکند، به عنوان چهارچوبی برای معنا دادن به تمرین\u200cهای این درسنامه ضروری است. اما انجام تمرین\u200cها است که هدف این دوره را ممکن می\u200cسازد. یک ذهن نیازموده هیچ کاری را نمی\u200cتواند به انجام رساند. قصد این درسنامه این است که ذهن تو را تمرین دهد تا در طول خطوطی که متن دوره می\u200cسازد، حرکت کند. \nتمرین\u200cها بسیار ساده هستند. زمان بسیار زیادی نمی\u200cطلبند، و فرقی نمی\u200cکند که کجا اجرا شوند. هیچ آمادگی نمی\u200cخواهند. دوره\u200cی آموزش یک سال است. تمرین\u200cها از ۱ تا ۳۶۵ شماره گذاری شده\u200cاند. در هر روز انجام بیش از یک دوره از تمرین\u200cها را به خود تحمیل نکن. \nاین درسنامه به دو بخش اصلی تقسیم شده است، بخش نخست با خنثی کردن شیوهٔ فعلی دیدن تو سروکار دارد، و بخش دوم \u200cبا کسب ادراک درست. به استثنای دوره\u200cهای مرور، تمرین\u200cهای هر روز پیرامون یک ایده\u200cی محوری طراحی شده\u200cاند که ابتدای هر درس بیان می\u200cشود. سپس به تشریح روندهای خاص تمرین با ا

In [54]:
with open('lesson_links.json', 'r', encoding='utf-8') as f:
    lessons = json.load(f)

for day, entries in en_fa_data.items():
    day_num = int(day)
    if len(entries) == 1:
        if day_num < len(lessons):
            entries[0]['textAddress']['en'] = lessons[day_num]
    elif len(entries) > 1:
        # Use lesson textAddress for the last entry if multiple entries exist
        if day_num < len(lessons):
            entries[-1]['textAddress']['en'] = lessons[day_num]

In [17]:
en_fa_data

{'0': [{'text': {'en': '',
    'fa': 'بنیانی نظری مانند آنچه که این متن [متنِ دوره\u200cای در معجزات] ایجاد می\u200cکند، به عنوان چهارچوبی برای معنا دادن به تمرین\u200cهای این درسنامه ضروری است. اما انجام تمرین\u200cها است که هدف این دوره را ممکن می\u200cسازد. یک ذهن نیازموده هیچ کاری را نمی\u200cتواند به انجام رساند. قصد این درسنامه این است که ذهن تو را تمرین دهد تا در طول خطوطی که متن دوره می\u200cسازد، حرکت کند. \nتمرین\u200cها بسیار ساده هستند. زمان بسیار زیادی نمی\u200cطلبند، و فرقی نمی\u200cکند که کجا اجرا شوند. هیچ آمادگی نمی\u200cخواهند. دوره\u200cی آموزش یک سال است. تمرین\u200cها از ۱ تا ۳۶۵ شماره گذاری شده\u200cاند. در هر روز انجام بیش از یک دوره از تمرین\u200cها را به خود تحمیل نکن. \nاین درسنامه به دو بخش اصلی تقسیم شده است، بخش نخست با خنثی کردن شیوهٔ فعلی دیدن تو سروکار دارد، و بخش دوم \u200cبا کسب ادراک درست. به استثنای دوره\u200cهای مرور، تمرین\u200cهای هر روز پیرامون یک ایده\u200cی محوری طراحی شده\u200cاند که ابتدای هر درس بیان می\u200cشود. سپس به تشریح روندهای خاص تمر

In [51]:
for day, entries in en_fa_data.items():
    day_num = int(day)
    print(f"Day {day_num}:")
    for entry in entries:
        textAddress = entry["textAddress"]["fa"]
        # take the last part starting from /workbook
        uri = textAddress[textAddress.rfind("/workbook"):]
        url = "https://acim-farsi.org/api/page/current?path=" + uri
        # get the data
        response = requests.get(url)
        if response.status_code == 200:
            data = response.json()
            entry['text']['en'] = extract_english_lesson_text(data)
            entry['text']['fa'] = extract_farsi_lesson_text(data)

Day 0:
Day 1:
Day 2:
Day 3:
Day 4:
Day 5:
Day 6:
Day 7:
Day 8:
Day 9:
Day 10:
Day 11:
Day 12:
Day 13:
Day 14:
Day 15:
Day 16:
Day 17:
Day 18:
Day 19:
Day 20:
Day 21:
Day 22:
Day 23:
Day 24:
Day 25:
Day 26:
Day 27:
Day 28:
Day 29:
Day 30:
Day 31:
Day 32:
Day 33:
Day 34:
Day 35:
Day 36:
Day 37:
Day 38:
Day 39:
Day 40:
Day 41:
Day 42:
Day 43:
Day 44:
Day 45:
Day 46:
Day 47:
Day 48:
Day 49:
Day 50:
Day 51:
Day 52:
Day 53:
Day 54:
Day 55:
Day 56:
Day 57:
Day 58:
Day 59:
Day 60:
Day 61:
Day 62:
Day 63:
Day 64:
Day 65:
Day 66:
Day 67:
Day 68:
Day 69:
Day 70:
Day 71:
Day 72:
Day 73:
Day 74:
Day 75:
Day 76:
Day 77:
Day 78:
Day 79:
Day 80:
Day 81:
Day 82:
Day 83:
Day 84:
Day 85:
Day 86:
Day 87:
Day 88:
Day 89:
Day 90:
Day 91:
Day 92:
Day 93:
Day 94:
Day 95:
Day 96:
Day 97:
Day 98:
Day 99:
Day 100:
Day 101:
Day 102:
Day 103:
Day 104:
Day 105:
Day 106:
Day 107:
Day 108:
Day 109:
Day 110:
Day 111:
Day 112:
Day 113:
Day 114:
Day 115:
Day 116:
Day 117:
Day 118:
Day 119:
Day 120:
Day 121:
Day 122:
Day

In [52]:
en_fa_data

{'0': [{'text': {'en': "A theoretical foundation such as the text provides is necessary as a framework to make the exercises in this workbook meaningful. Yet it is doing the exercises that will make the goal of the course possible. An untrained mind can accomplish nothing. It is the purpose of this workbook to train your mind to think along the lines the text sets forth.\n\nThe exercises are very simple. They do not require a great deal of time, and it does not matter where you do them. They need no preparation. The training period is one year. The exercises are numbered from 1 to 365. Do not undertake to do more than one set of exercises a day.\n\nThe workbook is divided into two main sections, the first dealing with the undoing of the way you see now, and the second with the acquisition of true perception. With the exception of the review periods, each day's exercises are planned around one central idea, which is stated first. This is followed by a description of the specific procedu

In [55]:
with open("DB_multilingual.json", "w", encoding="utf-8") as f:
    json.dump(en_fa_data, f, ensure_ascii=False, indent=4)

In [ ]:
import os
import re
import time
import random
import requests
import undetected_chromedriver as uc # Import the new library

def download_acim_audio_undetected(lesson_urls, output_dir="acim_workbook_audio"):
    """
    Downloads ACIM audio using undetected-chromedriver to bypass advanced WAFs.
    """
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
        print(f"Created directory: {output_dir}")

    # Use a requests session for the final download
    session = requests.Session()
    
    # Setup the undetected driver
    print("Setting up undetected browser driver...")
    options = uc.ChromeOptions()
    # Note: It's best to run WITHOUT headless mode first to ensure it works.
    # Some sites can detect headless mode.
    # options.add_argument('--headless') 
    driver = uc.Chrome(options=options, use_subprocess=True)
    print("Driver setup complete. The browser will now operate.")

    try:
        for url in lesson_urls:
            try:
                print(f"\nProcessing lesson: {url}")

                # 1. Navigate to the lesson page
                driver.get(url)

                # 2. Wait for the audio player to be present
                # Using a longer, more patient wait
                audio_element = driver.find_element(By.TAG_NAME, 'audio')

                # 3. Extract the direct audio source URL
                audio_url = audio_element.get_attribute('src')
                if not audio_url:
                    print("❌ Could not find audio source URL on the page.")
                    continue

                # 4. Generate filename
                match = re.search(r"lesson-\d+", url)
                filename = f"{match.group(0)}.mp3" if match else f"{url.strip('/').split('/')[-1]}.mp3"
                filepath = os.path.join(output_dir, filename)

                if os.path.exists(filepath):
                    print(f"File already exists: {filename}. Skipping.")
                    continue
                
                # 5. Transfer cookies from the browser to the requests session
                for cookie in driver.get_cookies():
                    session.cookies.set(cookie['name'], cookie['value'])

                print(f"Downloading {filename}...")
                
                # 6. Download the file with appropriate headers
                headers = {
                    'Referer': url,
                    'User-Agent': driver.execute_script("return navigator.userAgent;") # Use the browser's real UA
                }
                response = session.get(audio_url, headers=headers, stream=True)
                response.raise_for_status()

                with open(filepath, 'wb') as f:
                    for chunk in response.iter_content(chunk_size=8192):
                        f.write(chunk)

                print(f"✅ Successfully saved to {filepath}")

                # Use a random delay to appear more human
                sleep_time = random.uniform(3, 7)
                print(f"Pausing for {sleep_time:.1f} seconds...")
                time.sleep(sleep_time)

            except Exception as e:
                print(f"❌ An error occurred for URL {url}: {e}")
                # If one URL fails, wait before trying the next
                time.sleep(10)

    finally:
        # Ensure the browser is closed even if errors occur
        print("\nClosing browser.")
        driver.quit()

# --- HOW TO USE ---
if __name__ == "__main__":
    all_lesson_links = [
  "https://acim.org/acim/lesson-1/nothing-i-see-means-anything/en/s/403",
  "https://acim.org/acim/lesson-5/i-am-never-upset-for-the-reason-i-think/en/s/407",
  "https://acim.org/acim/lesson-6/i-am-upset-because-i-see-something-that-is-not-there/en/s/408",
  "https://acim.org/acim/lesson-11/my-meaningless-thoughts-are-showing-me-a/en/s/413",
  "https://acim.org/acim/lesson-14/god-did-not-create-a-meaningless-world/en/s/416",
  "https://acim.org/acim/lesson-15/my-thoughts-are-images-that-i-have-made/en/s/417",
  "https://acim.org/acim/lesson-16/i-have-no-neutral-thoughts/en/s/418",
  "https://acim.org/acim/lesson-17/i-see-no-neutral-things/en/s/419",
  "https://acim.org/acim/lesson-18/i-am-not-alone-in-experiencing-the-effects-of-my/en/s/420",
  "https://acim.org/acim/lesson-19/i-am-not-alone-in-experiencing-the-effects-of-my/en/s/421",
  "https://acim.org/acim/lesson-20/i-am-determined-to-see/en/s/422",
  "https://acim.org/acim/lesson-21/i-am-determined-to-see-things-differently/en/s/423",
  "https://acim.org/acim/lesson-22/what-i-see-is-a-form-of-vengeance/en/s/424",
  "https://acim.org/acim/lesson-23/i-can-escape-from-the-world-i-see-by-giving-up/en/s/425",
  "https://acim.org/acim/lesson-24/i-do-not-perceive-my-own-best-interests/en/s/426",
  "https://acim.org/acim/lesson-25/i-do-not-know-what-anything-is-for/en/s/427",
  "https://acim.org/acim/lesson-26/my-attack-thoughts-are-attacking-my/en/s/428",
  "https://acim.org/acim/lesson-27/above-all-else-i-want-to-see/en/s/429",
  "https://acim.org/acim/lesson-28/above-all-else-i-want-to-see-things-differently/en/s/430",
  "https://acim.org/acim/lesson-29/god-is-in-everything-i-see/en/s/431",
  "https://acim.org/acim/lesson-30/god-is-in-everything-i-see-because-god-is-in-my-mind/en/s/432",
  "https://acim.org/acim/lesson-31/i-am-not-the-victim-of-the-world-i-see/en/s/433",
  "https://acim.org/acim/lesson-32/i-have-invented-the-world-i-see/en/s/434",
  "https://acim.org/acim/lesson-33/there-is-another-way-of-looking-at-the-world/en/s/435",
  "https://acim.org/acim/lesson-34/i-could-see-peace-instead-of-this/en/s/436",
  "https://acim.org/acim/lesson-35/my-mind-is-part-of-gods-i-am-very-holy/en/s/437",
  "https://acim.org/acim/lesson-36/my-holiness-envelops-everything-i-see/en/s/438",
  "https://acim.org/acim/lesson-37/my-holiness-blesses-the-world/en/s/439",
  "https://acim.org/acim/lesson-38/there-is-nothing-my-holiness-cannot-do/en/s/440",
  "https://acim.org/acim/lesson-39/my-holiness-is-my-salvation/en/s/441",
  "https://acim.org/acim/lesson-40/i-am-blessed-as-a-son-of-god/en/s/442",
  "https://acim.org/acim/lesson-41/god-goes-with-me-wherever-i-go/en/s/443",
  "https://acim.org/acim/lesson-42/god-is-my-strength-vision-is-his-gift/en/s/444",
  "https://acim.org/acim/lesson-43/god-is-my-source-i-cannot-see-apart-from-him/en/s/445",
  "https://acim.org/acim/lesson-44/god-is-the-light-in-which-i-see/en/s/446",
  "https://acim.org/acim/lesson-45/god-is-the-mind-with-which-i-think/en/s/447",
  "https://acim.org/acim/lesson-46/god-is-the-love-in-which-i-forgive/en/s/448",
  "https://acim.org/acim/lesson-47/god-is-the-strength-in-which-i-trust/en/s/449",
  "https://acim.org/acim/lesson-48/there-is-nothing-to-fear/en/s/450",
  "https://acim.org/acim/lesson-49/gods-voice-speaks-to-me-all-through-the-day/en/s/451",
  "https://acim.org/acim/lesson-50/i-am-sustained-by-the-love-of-god/en/s/452",
  "https://acim.org/acim/review-i/lesson-51/en/s/454",
  "https://acim.org/acim/review-i/lesson-52/en/s/455",
  "https://acim.org/acim/review-i/lesson-53/en/s/456",
  "https://acim.org/acim/review-i/lesson-54/en/s/457",
  "https://acim.org/acim/review-i/lesson-55/en/s/458",
  "https://acim.org/acim/review-i/lesson-56/en/s/459",
  "https://acim.org/acim/review-i/lesson-57/en/s/460",
  "https://acim.org/acim/review-i/lesson-58/en/s/461",
  "https://acim.org/acim/review-i/lesson-59/en/s/462",
  "https://acim.org/acim/review-i/lesson-60/en/s/463",
  "https://acim.org/acim/lesson-61/i-am-the-light-of-the-world/en/s/464",
  "https://acim.org/acim/lesson-62/forgiveness-is-my-function-as-the-light-of-the/en/s/465",
  "https://acim.org/acim/lesson-63/the-light-of-the-world-brings-peace-to-every-mind/en/s/466",
  "https://acim.org/acim/lesson-64/let-me-not-forget-my-function/en/s/467",
  "https://acim.org/acim/lesson-65/my-only-function-is-the-one-god-gave-me/en/s/468",
  "https://acim.org/acim/lesson-66/my-happiness-and-my-function-are-one/en/s/469",
  "https://acim.org/acim/lesson-67/love-created-me-like-itself/en/s/470",
  "https://acim.org/acim/lesson-68/love-holds-no-grievances/en/s/471",
  "https://acim.org/acim/lesson-69/my-grievances-hide-the-light-of-the-world-in-me/en/s/472",
  "https://acim.org/acim/lesson-70/my-salvation-comes-from-me/en/s/473",
  "https://acim.org/acim/lesson-71/only-gods-plan-for-salvation-will-work/en/s/474",
  "https://acim.org/acim/lesson-72/holding-grievances-is-an-attack-on-gods-plan-for/en/s/475",
  "https://acim.org/acim/lesson-73/i-will-there-be-light/en/s/476",
  "https://acim.org/acim/lesson-74/there-is-no-will-but-gods/en/s/477",
  "https://acim.org/acim/lesson-75/the-light-has-come/en/s/478",
  "https://acim.org/acim/lesson-76/i-am-under-no-laws-but-gods/en/s/479",
  "https://acim.org/acim/lesson-77/i-am-entitled-to-miracles/en/s/480",
  "https://acim.org/acim/lesson-78/let-miracles-replace-all-grievances/en/s/481",
  "https://acim.org/acim/lesson-79/let-me-recognize-the-problem-so-it-can-be-solved/en/s/482",
  "https://acim.org/acim/lesson-80/let-me-recognize-my-problems-have-been-solved/en/s/483",
  "https://acim.org/acim/review-ii/lesson-81/en/s/485",
  "https://acim.org/acim/review-ii/lesson-82/en/s/486",
  "https://acim.org/acim/review-ii/lesson-83/en/s/487",
  "https://acim.org/acim/review-ii/lesson-84/en/s/488",
  "https://acim.org/acim/review-ii/lesson-85/en/s/489",
  "https://acim.org/acim/review-ii/lesson-86/en/s/490",
  "https://acim.org/acim/review-ii/lesson-87/en/s/491",
  "https://acim.org/acim/review-ii/lesson-88/en/s/492",
  "https://acim.org/acim/review-ii/lesson-89/en/s/493",
  "https://acim.org/acim/review-ii/lesson-90/en/s/494",
  "https://acim.org/acim/lesson-91/miracles-are-seen-in-light/en/s/495",
  "https://acim.org/acim/lesson-92/miracles-are-seen-in-light-and-light-and-strength/en/s/496",
  "https://acim.org/acim/lesson-93/light-and-joy-and-peace-abide-in-me/en/s/497",
  "https://acim.org/acim/lesson-94/i-am-as-god-created-me/en/s/498",
  "https://acim.org/acim/lesson-95/i-am-one-self-united-with-my-creator/en/s/499",
  "https://acim.org/acim/lesson-96/salvation-comes-from-my-one-self/en/s/500",
  "https://acim.org/acim/lesson-97/i-am-spirit/en/s/501",
  "https://acim.org/acim/lesson-98/i-will-accept-my-part-in-gods-plan-for-salvation/en/s/502",
  "https://acim.org/acim/lesson-99/salvation-is-my-only-function-here/en/s/503",
  "https://acim.org/acim/lesson-100/my-part-is-essential-to-gods-plan-for-salvation/en/s/504",
  "https://acim.org/acim/lesson-101/gods-will-for-me-is-perfect-happiness/en/s/505",
  "https://acim.org/acim/lesson-102/i-share-gods-will-for-happiness-for-me/en/s/506",
  "https://acim.org/acim/lesson-103/god-being-love-is-also-happiness/en/s/507",
  "https://acim.org/acim/lesson-104/i-seek-but-what-belongs-to-me-in-truth/en/s/508",
  "https://acim.org/acim/lesson-105/gods-peace-and-joy-are-mine/en/s/509",
  "https://acim.org/acim/lesson-106/let-me-be-still-and-listen-to-the-truth/en/s/510",
  "https://acim.org/acim/lesson-107/truth-will-correct-all-errors-in-my-mind/en/s/511",
  "https://acim.org/acim/lesson-108/to-give-and-to-receive-are-one-in-truth/en/s/512",
  "https://acim.org/acim/lesson-109/i-rest-in-god/en/s/513",
  "https://acim.org/acim/lesson-110/i-am-as-god-created-me/en/s/514",
  "https://acim.org/acim/review-iii/lesson-111/en/s/516",
  "https://acim.org/acim/review-iii/lesson-112/en/s/517",
  "https://acim.org/acim/review-iii/lesson-113/en/s/518",
  "https://acim.org/acim/review-iii/lesson-114/en/s/519",
  "https://acim.org/acim/review-iii/lesson-115/en/s/520",
  "https://acim.org/acim/review-iii/lesson-116/en/s/521",
  "https://acim.org/acim/review-iii/lesson-117/en/s/522",
  "https://acim.org/acim/review-iii/lesson-118/en/s/523",
  "https://acim.org/acim/review-iii/lesson-119/en/s/524",
  "https://acim.org/acim/review-iii/lesson-120/en/s/525",
  "https://acim.org/acim/lesson-121/forgiveness-is-the-key-to-happiness/en/s/526",
  "https://acim.org/acim/lesson-122/forgiveness-offers-everything-i-want/en/s/527",
  "https://acim.org/acim/lesson-123/i-thank-my-father-for-his-gifts-to-me/en/s/528",
  "https://acim.org/acim/lesson-124/let-me-remember-i-am-one-with-god/en/s/529",
  "https://acim.org/acim/lesson-125/in-quiet-i-receive-gods-word-today/en/s/530",
  "https://acim.org/acim/lesson-126/all-that-i-give-is-given-to-myself/en/s/531",
  "https://acim.org/acim/lesson-127/there-is-no-love-but-gods/en/s/532",
  "https://acim.org/acim/lesson-128/the-world-i-see-holds-nothing-that-i-want/en/s/533",
  "https://acim.org/acim/lesson-129/beyond-this-world-there-is-a-world-i-want/en/s/534",
  "https://acim.org/acim/lesson-130/it-is-impossible-to-see-two-worlds/en/s/535",
  "https://acim.org/acim/lesson-131/no-one-can-fail-who-seeks-to-reach-the-truth/en/s/536",
  "https://acim.org/acim/lesson-132/i-loose-the-world-from-all-i-thought-it-was/en/s/537",
  "https://acim.org/acim/lesson-133/i-will-not-value-what-is-valueless/en/s/538",
  "https://acim.org/acim/lesson-134/let-me-perceive-forgiveness-as-it-is/en/s/539",
  "https://acim.org/acim/lesson-135/if-i-defend-myself-i-am-attacked/en/s/540",
  "https://acim.org/acim/lesson-136/sickness-is-a-defense-against-the-truth/en/s/541",
  "https://acim.org/acim/lesson-137/when-i-am-healed-i-am-not-healed-alone/en/s/542",
  "https://acim.org/acim/lesson-138/heaven-is-the-decision-i-must-make/en/s/543",
  "https://acim.org/acim/lesson-139/i-will-accept-atonement-for-myself/en/s/544",
  "https://acim.org/acim/lesson-140/only-salvation-can-be-said-to-cure/en/s/545",
  "https://acim.org/acim/review-iv/lesson-141/en/s/547",
  "https://acim.org/acim/review-iv/lesson-142/en/s/548",
  "https://acim.org/acim/review-iv/lesson-143/en/s/549",
  "https://acim.org/acim/review-iv/lesson-144/en/s/550",
  "https://acim.org/acim/review-iv/lesson-145/en/s/551",
  "https://acim.org/acim/review-iv/lesson-146/en/s/552",
  "https://acim.org/acim/review-iv/lesson-147/en/s/553",
  "https://acim.org/acim/review-iv/lesson-148/en/s/554",
  "https://acim.org/acim/review-iv/lesson-149/en/s/555",
  "https://acim.org/acim/review-iv/lesson-150/en/s/556",
  "https://acim.org/acim/lesson-151/all-things-are-echoes-of-the-voice-for-god/en/s/557",
  "https://acim.org/acim/lesson-152/the-power-of-decision-is-my-own/en/s/558",
  "https://acim.org/acim/lesson-153/in-my-defenselessness-my-safety-lies/en/s/559",
  "https://acim.org/acim/lesson-154/i-am-among-the-ministers-of-god/en/s/560",
  "https://acim.org/acim/lesson-155/i-will-step-back-and-let-him-lead-the-way/en/s/561",
  "https://acim.org/acim/lesson-156/i-walk-with-god-in-perfect-holiness/en/s/562",
  "https://acim.org/acim/lesson-157/into-his-presence-would-i-enter-now/en/s/563",
  "https://acim.org/acim/lesson-158/today-i-learn-to-give-as-i-receive/en/s/564",
  "https://acim.org/acim/lesson-159/i-give-the-miracles-i-have-received/en/s/565",
  "https://acim.org/acim/lesson-160/i-am-at-home-fear-is-the-stranger-here/en/s/566",
  "https://acim.org/acim/lesson-161/give-me-your-blessing-holy-son-of-god/en/s/567",
  "https://acim.org/acim/lesson-162/i-am-as-god-created-me/en/s/568",
  "https://acim.org/acim/lesson-163/there-is-no-death-the-son-of-god-is-free/en/s/569",
  "https://acim.org/acim/lesson-164/now-are-we-one-with-him-who-is-our-source/en/s/570",
  "https://acim.org/acim/lesson-165/let-not-my-mind-deny-the-thought-of-god/en/s/571",
  "https://acim.org/acim/lesson-166/i-am-entrusted-with-the-gifts-of-god/en/s/572",
  "https://acim.org/acim/lesson-167/there-is-one-life-and-that-i-share-with-god/en/s/573",
  "https://acim.org/acim/lesson-168/your-grace-is-given-me-i-claim-it-now/en/s/574",
  "https://acim.org/acim/lesson-169/by-grace-i-live-by-grace-i-am-released/en/s/575",
  "https://acim.org/acim/lesson-170/there-is-no-cruelty-in-god-and-none-in-me/en/s/576",
  "https://acim.org/acim/review-v/lesson-171/en/s/578",
  "https://acim.org/acim/review-v/lesson-172/en/s/579",
  "https://acim.org/acim/review-v/lesson-173/en/s/580",
  "https://acim.org/acim/review-v/lesson-174/en/s/581",
  "https://acim.org/acim/review-v/lesson-175/en/s/582",
  "https://acim.org/acim/review-v/lesson-176/en/s/583",
  "https://acim.org/acim/review-v/lesson-177/en/s/584",
  "https://acim.org/acim/review-v/lesson-178/en/s/585",
  "https://acim.org/acim/review-v/lesson-179/en/s/586",
  "https://acim.org/acim/review-v/lesson-180/en/s/587",
  "https://acim.org/acim/lesson-181/i-trust-my-brothers-who-are-one-with-me/en/s/589",
  "https://acim.org/acim/lesson-182/i-will-be-still-an-instant-and-go-home/en/s/590",
  "https://acim.org/acim/lesson-183/i-call-upon-gods-name-and-on-my-own/en/s/591",
  "https://acim.org/acim/lesson-184/the-name-of-god-is-my-inheritance/en/s/592",
  "https://acim.org/acim/lesson-185/i-want-the-peace-of-god/en/s/593",
  "https://acim.org/acim/lesson-186/salvation-of-the-world-depends-on-me/en/s/594",
  "https://acim.org/acim/lesson-187/i-bless-the-world-because-i-bless-myself/en/s/595",
  "https://acim.org/acim/lesson-188/the-peace-of-god-is-shining-in-me-now/en/s/596",
  "https://acim.org/acim/lesson-189/i-feel-the-love-of-god-within-me-now/en/s/597",
  "https://acim.org/acim/lesson-190/i-choose-the-joy-of-god-instead-of-pain/en/s/598",
  "https://acim.org/acim/lesson-191/i-am-the-holy-son-of-god-himself/en/s/599",
  "https://acim.org/acim/lesson-192/i-have-a-function-god-would-have-me-fill/en/s/600",
  "https://acim.org/acim/lesson-193/all-things-are-lessons-god-would-have-me-learn/en/s/601",
  "https://acim.org/acim/lesson-194/i-place-the-future-in-the-hands-of-god/en/s/602",
  "https://acim.org/acim/lesson-195/love-is-the-way-i-walk-in-gratitude/en/s/603",
  "https://acim.org/acim/lesson-196/it-can-be-but-myself-i-crucify/en/s/604",
  "https://acim.org/acim/lesson-197/it-can-be-but-my-gratitude-i-earn/en/s/605",
  "https://acim.org/acim/lesson-198/only-my-condemnation-injures-me/en/s/606",
  "https://acim.org/acim/lesson-199/i-am-not-a-body-i-am-free/en/s/607",
  "https://acim.org/acim/lesson-200/there-is-no-peace-except-the-peace-of-god/en/s/608",
  "https://acim.org/acim/review-vi/lesson-201/en/s/610",
  "https://acim.org/acim/review-vi/lesson-202/en/s/611",
  "https://acim.org/acim/review-vi/lesson-203/en/s/612",
  "https://acim.org/acim/review-vi/lesson-204/en/s/613",
  "https://acim.org/acim/review-vi/lesson-205/en/s/614",
  "https://acim.org/acim/review-vi/lesson-206/en/s/615",
  "https://acim.org/acim/review-vi/lesson-207/en/s/616",
  "https://acim.org/acim/review-vi/lesson-208/en/s/617",
  "https://acim.org/acim/review-vi/lesson-209/en/s/618",
  "https://acim.org/acim/review-vi/lesson-210/en/s/619",
  "https://acim.org/acim/review-vi/lesson-211/en/s/620",
  "https://acim.org/acim/review-vi/lesson-212/en/s/621",
  "https://acim.org/acim/review-vi/lesson-213/en/s/622",
  "https://acim.org/acim/review-vi/lesson-214/en/s/623",
  "https://acim.org/acim/review-vi/lesson-215/en/s/624",
  "https://acim.org/acim/review-vi/lesson-216/en/s/625",
  "https://acim.org/acim/review-vi/lesson-217/en/s/626",
  "https://acim.org/acim/review-vi/lesson-218/en/s/627",
  "https://acim.org/acim/review-vi/lesson-219/en/s/628",
  "https://acim.org/acim/review-vi/lesson-220/en/s/629",
  "https://acim.org/acim/lesson-221/peace-to-my-mind-let-all-my-thoughts-be-still/en/s/633",
  "https://acim.org/acim/lesson-222/god-is-with-me-i-live-and-move-in-him/en/s/634",
  "https://acim.org/acim/lesson-223/god-is-my-life-i-have-no-life-but-his/en/s/635",
  "https://acim.org/acim/lesson-224/god-is-my-father-and-he-loves-his-son/en/s/636",
  "https://acim.org/acim/lesson-225/god-is-my-father-and-his-son-loves-him/en/s/637",
  "https://acim.org/acim/lesson-226/my-home-awaits-me-i-will-hasten-there/en/s/638",
  "https://acim.org/acim/lesson-227/this-is-my-holy-instant-of-release/en/s/639",
  "https://acim.org/acim/lesson-228/god-has-condemned-me-not-no-more-do-i/en/s/640",
  "https://acim.org/acim/lesson-229/love-which-created-me-is-what-i-am/en/s/641",
  "https://acim.org/acim/lesson-230/now-will-i-seek-and-find-the-peace-of-god/en/s/642",
  "https://acim.org/acim/lesson-231/father-i-will-but-to-remember-you/en/s/644",
  "https://acim.org/acim/lesson-232/be-in-my-mind-my-father-through-the-day/en/s/645",
  "https://acim.org/acim/lesson-233/i-give-my-life-to-god-to-guide-today/en/s/646",
  "https://acim.org/acim/lesson-234/father-today-i-am-your-son-again/en/s/647",
  "https://acim.org/acim/lesson-235/god-in-his-mercy-wills-that-i-be-saved/en/s/648",
  "https://acim.org/acim/lesson-236/i-rule-my-mind-which-i-alone-must-rule/en/s/649",
  "https://acim.org/acim/lesson-237/now-would-i-be-as-god-created-me/en/s/650",
  "https://acim.org/acim/lesson-238/on-my-decision-all-salvation-rests/en/s/651",
  "https://acim.org/acim/lesson-239/the-glory-of-my-father-is-my-own/en/s/652",
  "https://acim.org/acim/lesson-240/fear-is-not-justified-in-any-form/en/s/653",
  "https://acim.org/acim/lesson-241/this-holy-instant-is-salvation-come/en/s/655",
  "https://acim.org/acim/lesson-242/this-day-is-gods-it-is-my-gift-to-him/en/s/656",
  "https://acim.org/acim/lesson-243/today-i-will-judge-nothing-that-occurs/en/s/657",
  "https://acim.org/acim/lesson-244/i-am-in-danger-nowhere-in-the-world/en/s/658",
  "https://acim.org/acim/lesson-245/your-peace-is-with-me-father-i-am-safe/en/s/659",
  "https://acim.org/acim/lesson-246/to-love-my-father-is-to-love-his-son/en/s/660",
  "https://acim.org/acim/lesson-247/without-forgiveness-i-will-still-be-blind/en/s/661",
  "https://acim.org/acim/lesson-248/whatever-suffers-is-not-part-of-me/en/s/662",
  "https://acim.org/acim/lesson-249/forgiveness-ends-all-suffering-and-loss/en/s/663",
  "https://acim.org/acim/lesson-250/let-me-not-see-myself-as-limited/en/s/664",
  "https://acim.org/acim/lesson-251/i-am-in-need-of-nothing-but-the-truth/en/s/666",
  "https://acim.org/acim/lesson-252/the-son-of-god-is-my-identity/en/s/667",
  "https://acim.org/acim/lesson-253/my-self-is-ruler-of-the-universe/en/s/668",
  "https://acim.org/acim/lesson-254/let-every-voice-but-gods-be-still-in-me/en/s/669",
  "https://acim.org/acim/lesson-255/this-day-i-choose-to-spend-in-perfect-peace/en/s/670",
  "https://acim.org/acim/lesson-256/god-is-the-only-goal-i-have-today/en/s/671",
  "https://acim.org/acim/lesson-257/let-me-remember-what-my-purpose-is/en/s/672",
  "https://acim.org/acim/lesson-258/let-me-remember-that-my-goal-is-god/en/s/673",
  "https://acim.org/acim/lesson-259/let-me-remember-that-there-is-no-sin/en/s/674",
  "https://acim.org/acim/lesson-260/let-me-remember-god-created-me/en/s/675",
  "https://acim.org/acim/lesson-261/god-is-my-refuge-and-security/en/s/677",
  "https://acim.org/acim/lesson-262/let-me-perceive-no-differences-today/en/s/678",
  "https://acim.org/acim/lesson-263/my-holy-vision-sees-all-things-as-pure/en/s/679",
  "https://acim.org/acim/lesson-264/i-am-surrounded-by-the-love-of-god/en/s/680",
  "https://acim.org/acim/lesson-265/creations-gentleness-is-all-i-see/en/s/681",
  "https://acim.org/acim/lesson-266/my-holy-self-abides-in-you-gods-son/en/s/682",
  "https://acim.org/acim/lesson-267/my-heart-is-beating-in-the-peace-of-god/en/s/683",
  "https://acim.org/acim/lesson-268/let-all-things-be-exactly-as-they-are/en/s/684",
  "https://acim.org/acim/lesson-269/my-sight-goes-forth-to-look-upon-christs-face/en/s/685",
  "https://acim.org/acim/lesson-270/i-will-not-use-the-bodys-eyes-today/en/s/686",
  "https://acim.org/acim/lesson-271/christs-is-the-vision-i-will-use-today/en/s/688",
  "https://acim.org/acim/lesson-272/how-can-illusions-satisfy-gods-son/en/s/689",
  "https://acim.org/acim/lesson-273/the-stillness-of-the-peace-of-god-is-mine/en/s/690",
  "https://acim.org/acim/lesson-274/today-belongs-to-love-let-me-not-fear/en/s/691",
  "https://acim.org/acim/lesson-275/gods-healing-voice-protects-all-things-today/en/s/692",
  "https://acim.org/acim/lesson-276/the-word-of-god-is-given-me-to-speak/en/s/693",
  "https://acim.org/acim/lesson-277/let-me-not-bind-your-son-with-laws-i-made/en/s/694",
  "https://acim.org/acim/lesson-278/if-i-am-bound-my-father-is-not-free/en/s/695",
  "https://acim.org/acim/lesson-279/creations-freedom-promises-my-own/en/s/696",
  "https://acim.org/acim/lesson-280/what-limits-can-i-lay-upon-gods-son/en/s/697",
  "https://acim.org/acim/lesson-281/i-can-be-hurt-by-nothing-but-my-thoughts/en/s/699",
  "https://acim.org/acim/lesson-282/i-will-not-be-afraid-of-love-today/en/s/700",
  "https://acim.org/acim/lesson-283/my-true-identity-abides-in-you/en/s/701",
  "https://acim.org/acim/lesson-284/i-can-elect-to-change-all-thoughts-that-hurt/en/s/702",
  "https://acim.org/acim/lesson-285/my-holiness-shines-bright-and-clear-today/en/s/703",
  "https://acim.org/acim/lesson-286/the-hush-of-heaven-holds-my-heart-today/en/s/704",
  "https://acim.org/acim/lesson-287/you-are-my-goal-my-father-only-you/en/s/705",
  "https://acim.org/acim/lesson-288/let-me-forget-my-brothers-past-today/en/s/706",
  "https://acim.org/acim/lesson-289/the-past-is-over-it-can-touch-me-not/en/s/707",
  "https://acim.org/acim/lesson-290/my-present-happiness-is-all-i-see/en/s/708",
  "https://acim.org/acim/lesson-291/this-is-a-day-of-stillness-and-of-peace/en/s/710",
  "https://acim.org/acim/lesson-292/a-happy-outcome-to-all-things-is-sure/en/s/711",
  "https://acim.org/acim/lesson-293/all-fear-is-past-and-only-love-is-here/en/s/712",
  "https://acim.org/acim/lesson-294/my-body-is-a-wholly-neutral-thing/en/s/713",
  "https://acim.org/acim/lesson-295/the-holy-spirit-looks-through-me-today/en/s/714",
  "https://acim.org/acim/lesson-296/the-holy-spirit-speaks-through-me-today/en/s/715",
  "https://acim.org/acim/lesson-297/forgiveness-is-the-only-gift-i-give/en/s/716",
  "https://acim.org/acim/lesson-298/i-love-you-father-and-i-love-your-son/en/s/717",
  "https://acim.org/acim/lesson-299/eternal-holiness-abides-in-me/en/s/718",
  "https://acim.org/acim/lesson-300/only-an-instant-does-this-world-endure/en/s/719",
  "https://acim.org/acim/lesson-301/and-god-himself-shall-wipe-away-all-tears/en/s/721",
  "https://acim.org/acim/lesson-302/where-darkness-was-i-look-upon-the-light/en/s/722",
  "https://acim.org/acim/lesson-303/the-holy-christ-is-born-in-me-today/en/s/723",
  "https://acim.org/acim/lesson-304/let-not-my-world-obscure-the-sight-of-christ/en/s/724",
  "https://acim.org/acim/lesson-305/there-is-a-peace-that-christ-bestows-on-us/en/s/725",
  "https://acim.org/acim/lesson-306/the-gift-of-christ-is-all-i-seek-today/en/s/726",
  "https://acim.org/acim/lesson-307/conflicting-wishes-cannot-be-my-will/en/s/727",
  "https://acim.org/acim/lesson-308/this-instant-is-the-only-time-there-is/en/s/728",
  "https://acim.org/acim/lesson-309/i-will-not-fear-to-look-within-today/en/s/729",
  "https://acim.org/acim/lesson-310/in-fearlessness-and-love-i-spend-today/en/s/730",
  "https://acim.org/acim/lesson-311/i-judge-all-things-as-i-would-have-them-be/en/s/732",
  "https://acim.org/acim/lesson-312/i-see-all-things-as-i-would-have-them-be/en/s/733",
  "https://acim.org/acim/lesson-313/now-let-a-new-perception-come-to-me/en/s/734",
  "https://acim.org/acim/lesson-314/i-seek-a-future-different-from-the-past/en/s/735",
  "https://acim.org/acim/lesson-315/all-gifts-my-brothers-give-belong-to-me/en/s/736",
  "https://acim.org/acim/lesson-316/all-gifts-i-give-my-brothers-are-my-own/en/s/737",
  "https://acim.org/acim/lesson-317/i-follow-in-the-way-appointed-me/en/s/738",
  "https://acim.org/acim/lesson-318/in-me-salvations-means-and-end-are-one/en/s/739",
  "https://acim.org/acim/lesson-319/i-came-for-the-salvation-of-the-world/en/s/740",
  "https://acim.org/acim/lesson-320/my-father-gives-all-power-unto-me/en/s/741",
  "https://acim.org/acim/lesson-321/father-my-freedom-is-in-you-alone/en/s/743",
  "https://acim.org/acim/lesson-322/i-can-give-up-but-what-was-never-real/en/s/744",
  "https://acim.org/acim/lesson-323/i-gladly-make-the-sacrifice-of-fear/en/s/745",
  "https://acim.org/acim/lesson-324/i-merely-follow-for-i-would-not-lead/en/s/746",
  "https://acim.org/acim/lesson-325/all-things-i-think-i-see-reflect-ideas/en/s/747",
  "https://acim.org/acim/lesson-326/i-am-forever-an-effect-of-god/en/s/748",
  "https://acim.org/acim/lesson-327/i-need-but-call-and-you-will-answer-me/en/s/749",
  "https://acim.org/acim/lesson-328/i-choose-the-second-place-to-gain-the-first/en/s/750",
  "https://acim.org/acim/lesson-329/i-have-already-chosen-what-you-will/en/s/751",
  "https://acim.org/acim/lesson-330/i-will-not-hurt-myself-again-today/en/s/752",
  "https://acim.org/acim/lesson-331/there-is-no-conflict-for-my-will-is-yours/en/s/754",
  "https://acim.org/acim/lesson-332/fear-binds-the-world-forgiveness-sets-it-free/en/s/755",
  "https://acim.org/acim/lesson-333/forgiveness-ends-the-dream-of-conflict-here/en/s/756",
  "https://acim.org/acim/lesson-334/today-i-claim-the-gifts-forgiveness-gives/en/s/757",
  "https://acim.org/acim/lesson-335/i-choose-to-see-my-brothers-sinlessness/en/s/758",
  "https://acim.org/acim/lesson-336/forgiveness-lets-me-know-that-minds-are-joined/en/s/759",
  "https://acim.org/acim/lesson-337/my-sinlessness-protects-me-from-all-harm/en/s/760",
  "https://acim.org/acim/lesson-338/i-am-affected-only-by-my-thoughts/en/s/761",
  "https://acim.org/acim/lesson-339/i-will-receive-whatever-i-request/en/s/762",
  "https://acim.org/acim/lesson-340/i-can-be-free-of-suffering-today/en/s/763",
  "https://acim.org/acim/lesson-341/i-can-attack-but-my-own-sinlessness-and-it-is-only/en/s/765",
  "https://acim.org/acim/lesson-342/i-let-forgiveness-rest-upon-all-things-for-thus/en/s/766",
  "https://acim.org/acim/lesson-343/i-am-not-asked-to-make-a-sacrifice-to-find-the/en/s/767",
  "https://acim.org/acim/lesson-344/today-i-learn-the-law-of-love-that-what-i-give-my/en/s/768",
  "https://acim.org/acim/lesson-345/i-offer-only-miracles-today-for-i-would-have-them/en/s/769",
  "https://acim.org/acim/lesson-346/today-the-peace-of-god-envelops-me-and-i-forget/en/s/770",
  "https://acim.org/acim/lesson-347/anger-must-come-from-judgment-judgment-is-the/en/s/771",
  "https://acim.org/acim/lesson-348/i-have-no-cause-for-anger-or-for-fear-for-you/en/s/772",
  "https://acim.org/acim/lesson-349/today-i-let-christs-vision-look-upon-all-things/en/s/773",
  "https://acim.org/acim/lesson-350/miracles-mirror-gods-eternal-love-to-offer-them/en/s/774",
  "https://acim.org/acim/lesson-351/my-sinless-brother-is-my-guide-to-peace-my-sinful/en/s/776",
  "https://acim.org/acim/lesson-352/judgment-and-love-are-opposites-from-one-come/en/s/777",
  "https://acim.org/acim/lesson-353/my-eyes-my-tongue-my-hands-my-feet-today-have-but/en/s/778",
  "https://acim.org/acim/lesson-354/we-stand-together-christ-and-i-in-peace-and/en/s/779",
  "https://acim.org/acim/lesson-355/there-is-no-end-to-all-the-peace-and-joy-and-all-the/en/s/780",
  "https://acim.org/acim/lesson-356/sickness-is-but-another-name-for-sin-healing-is/en/s/781",
  "https://acim.org/acim/lesson-357/truth-answers-every-call-we-make-to-god/en/s/782",
  "https://acim.org/acim/lesson-358/no-call-to-god-can-be-unheard-nor-left-unanswered/en/s/783",
  "https://acim.org/acim/lesson-359/gods-answer-is-some-form-of-peace-all-pain-is/en/s/784",
  "https://acim.org/acim/lesson-360/peace-be-to-me-the-holy-son-of-god-peace-to-my/en/s/785",
  "https://acim.org/acim/final-lessons/lessons-361-to-365/en/s/787"
]

    download_acim_audio_undetected(all_lesson_links)
    print("\n🎉 All downloads complete!")

Setting up undetected browser driver...
Driver setup complete. The browser will now operate.

Processing lesson: https://acim.org/acim/lesson-1/nothing-i-see-means-anything/en/s/403
❌ An error occurred for URL https://acim.org/acim/lesson-1/nothing-i-see-means-anything/en/s/403: Message: no such element: Unable to locate element: {"method":"tag name","selector":"audio"}
  (Session info: chrome=138.0.7204.169); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#nosuchelementexception
Stacktrace:
0   undetected_chromedriver             0x0000000100ea1a98 undetected_chromedriver + 6167192
1   undetected_chromedriver             0x0000000100e9904a undetected_chromedriver + 6131786
2   undetected_chromedriver             0x0000000100925e00 undetected_chromedriver + 417280
3   undetected_chromedriver             0x0000000100977c74 undetected_chromedriver + 752756
4   undetected_chromedriver             0x0000000100977e91 und

KeyboardInterrupt: 

In [3]:
import json
with open("DB_multilingual_new_2.json", "r", encoding="utf-8") as f:
    multilingual_data_2 = json.load(f)

In [4]:
import json
with open("DB_multilingual_new_3.json", "r", encoding="utf-8") as f:
    multilingual_data_3 = json.load(f)

In [5]:
def merge_nested_objects(obj1, obj2):
    """
    Recursively merges two nested objects (dictionaries or lists).

    The logic is as follows:
    - If both are dictionaries, it merges them key by key.
    - If both are lists, it merges them element by element, assuming
      they have the same length.
    - If one object has a value and the other is an empty string,
      it uses the value that is not an empty string.
    - Otherwise, it defaults to the value from the first object (obj1).

    Args:
        obj1: The first object (dictionary, list, or value).
        obj2: The second object (dictionary, list, or value).

    Returns:
        A new object with merged values.
    """
    # Base case: if the objects are not dictionaries or lists,
    # apply the core merging logic.
    if not isinstance(obj1, (dict, list)) or not isinstance(obj2, (dict, list)):
        # If obj1 is a non-empty string and obj2 is empty, use obj1.
        if isinstance(obj1, str) and isinstance(obj2, str) and obj1 and not obj2:
            return obj1
        # If obj2 is a non-empty string and obj1 is empty, use obj2.
        elif isinstance(obj1, str) and isinstance(obj2, str) and obj2 and not obj1:
            return obj2
        # Otherwise, default to obj1's value.
        else:
            return obj1

    # Recursive case for dictionaries
    if isinstance(obj1, dict) and isinstance(obj2, dict):
        merged_dict = {}
        all_keys = set(obj1.keys()) | set(obj2.keys())
        for key in all_keys:
            # Use .get() to handle cases where a key might be missing in one of the dictionaries
            val1 = obj1.get(key)
            val2 = obj2.get(key)
            merged_dict[key] = merge_nested_objects(val1, val2)
        return merged_dict

    # Recursive case for lists
    if isinstance(obj1, list) and isinstance(obj2, list):
        merged_list = []
        # Assuming lists have the same length for merging.
        # You can add logic here to handle different lengths if needed.
        for i in range(min(len(obj1), len(obj2))):
            merged_list.append(merge_nested_objects(obj1[i], obj2[i]))
        return merged_list

    # Default return for any unhandled cases (e.g., mixed types)
    return obj1



In [6]:
multilingual_data = merge_nested_objects(multilingual_data_2, multilingual_data_3)

In [3]:
multilingual_data["0"]

[{'text': {'en': "A theoretical foundation such as the text provides is necessary as a framework to make the exercises in this workbook meaningful. Yet it is doing the exercises that will make the goal of the course possible. An untrained mind can accomplish nothing. It is the purpose of this workbook to train your mind to think along the lines the text sets forth.\n\nThe exercises are very simple. They do not require a great deal of time, and it does not matter where you do them. They need no preparation. The training period is one year. The exercises are numbered from 1 to 365. Do not undertake to do more than one set of exercises a day.\n\nThe workbook is divided into two main sections, the first dealing with the undoing of the way you see now, and the second with the acquisition of true perception. With the exception of the review periods, each day's exercises are planned around one central idea, which is stated first. This is followed by a description of the specific procedures by

In [46]:
import re
import time
def extract_json_from_text(text):
        """Extracts the first valid JSON object from the text."""
        try:
            match = re.search(r'{.*}', text, re.DOTALL)
            if match:
                json_str = match.group(0)
                json_str = json_str.replace("“", '"').replace("”", '"').replace("‘", "'").replace("’", "'")
                return json.loads(json_str)
        except json.JSONDecodeError:
            return None
        return None

def translateRepetitionTextToPersian(persianText, englishText, englishRepetitionText, max_retries=10, delay=2):
    attempts = 0
    while attempts < max_retries:
        completion = client.chat.completions.create(
            model="gpt-4o",
            messages = [{
                "role": "system",
                "content": f"""Considering the following Persian translation of this ACIM workbook lesson, please translate this english repetition text to Persian. Please try to use same wordings of persian translation of lesson in the translation of repetition text to persian.

                english workbook lesson: {englishText}
                persian workbook lesson: {persianText}
                english repetition text: {englishRepetitionText}

                The output must be a valid JSON—no explanation, no extra text. Format:
                {{
                "persian repetition text": "..."
                }}
                """
            }]
        )

        result = completion.choices[0].message.content
        parsed = extract_json_from_text(result)
        if parsed:
            return parsed
    
        print("Failed to decode JSON")
        print(result)
        attempts += 1
        time.sleep(delay)
    return {"error": "Failed to decode JSON after multiple attempts"}

def translateTitleToPersian(persianText, englishText, englishTitle, max_retries=10, delay=2):
    attempts = 0
    while attempts < max_retries:
        completion = client.chat.completions.create(
            model="gpt-4o",
            messages = [{
                "role": "system",
                "content": f"""Considering the following Persian translation of this ACIM workbook lesson, please translate the title to Persian.

                english text: {englishText}
                persian text: {persianText}
                english title: {englishTitle}

                The output must be a valid JSON—no explanation, no extra text. Format:
                {{
                "persian title": "..."
                }}
                """
            }]
        )

        result = completion.choices[0].message.content
        parsed = extract_json_from_text(result)
        if parsed:
            return parsed
    
        print("Failed to decode JSON")
        print(result)
        attempts += 1
        time.sleep(delay)
    return {"error": "Failed to decode JSON after multiple attempts"}

In [ ]:
import tqdm
for day_entries in tqdm.tqdm(multilingual_data.values()):
    for entry in day_entries:
        text = entry["text"]
        result = translateRepetitionTextToPersian(entry["text"]["fa"], entry["text"]["en"], entry["repetitionText"]["en"])
        entry["repetitionText"]["fa"] = result["persian repetition text"]

    # save to file as you are processing to update the  newDB.json file with latest content of output_data
    with open("DB_multilingual_new_3.json", "w", encoding="utf-8") as f:
        json.dump(multilingual_data, f, ensure_ascii=False, indent=4)


  0%|          | 0/366 [00:00<?, ?it/s]

 11%|█         | 41/366 [01:21<17:17,  3.19s/it]

Failed to decode JSON
I'm sorry, I can only assist with English text.


 14%|█▍        | 51/366 [01:43<07:07,  1.36s/it]

Failed to decode JSON
```json
{
"persian repetition text": "(6) من از این جهت آشفته‌ام که چیزی را می‌بینم که وجود ندارد.
(7) من تنها گذشته را می‌بینم.
(8) ذهن من با افکار گذشته مشغول است.
(9) من هیچ‌چیز را به‌گونه‌ای که اکنون هست نمی‌بینم.
(10) افکار من معنایی ندارند."
}
```


 73%|███████▎  | 268/366 [15:34<04:19,  2.64s/it]

In [15]:
#open ACIM Alarm.csv into a dataframe
# import pandas as pd
# df = pd.read_csv("ACIM Alarm.csv")
for day_index, day_entries in enumerate(tqdm.tqdm(multilingual_data.values())):
    for entry in day_entries:
        # delete repetitionTextShort and repetitionTextLong
        try:
            del entry["videoAddress"]
            del entry["repetitionTextShort"]
            del entry["repetitionTextLong"]
        except KeyError:
            pass
        # use df to get the repetitionText
        # entry["repetitionText"]["en"] = df[df["day"] == day_index + 1]["long"].values[0]


100%|██████████| 366/366 [00:00<00:00, 471038.74it/s]


In [41]:
with open("DB_multilingual_new_2.json", "w", encoding="utf-8") as f:
    json.dump(multilingual_data, f, ensure_ascii=False, indent=4)


In [40]:
import pandas as pd
df = pd.read_csv("ACIM Alarm.csv")

for day_index, day_entries in enumerate(tqdm.tqdm(multilingual_data.values())):
    if(day_index == 0):
        continue
    day_entries[-1]["repetitionText"]["en"] = df[df["day"] == day_index]["long"].values[0]

100%|██████████| 366/366 [00:00<00:00, 6799.56it/s]


In [39]:
day_index

0

In [34]:
df[df["day"] == day_index + 1]

Empty DataFrame
Columns: [day, repetition code, short, long, Unnamed: 4, Unnamed: 5]
Index: []

In [30]:
df[df["day"] ==  1]["long"].values[0]

'This table does not mean anything.\nThis chair does not mean anything.\nThis hand does not mean anything.\nThis foot does not mean anything.\nThis pen does not mean anything.\n\nThat door does not mean anything.\nThat body does not mean anything.\nThat lamp does not mean anything.\nThat sign does not mean anything.\nThat shadow does not mean anything.'

In [25]:
multilingual_data["1"]

[{'text': {'en': 'Nothing I see in this room [on this street, from this window, in this place] means anything.\n\nNow look slowly around you, and practice applying this idea very specifically to whatever you see: This table does not mean anything. This chair does not mean anything. This hand does not mean anything. This foot does not mean anything. This pen does not mean anything.\n\nThen look farther away from your immediate area, and apply the idea to a wider range: That door does not mean anything. That body does not mean anything. That lamp does not mean anything. That sign does not mean anything. That shadow does not mean anything.\n\nNotice that these statements are not arranged in any order, and make no allowance for differences in the kinds of things to which they are applied. That is the purpose of the exercise. The statement should merely be applied to anything you see. As you practice the idea for the day, use it totally indiscriminately. Do not attempt to apply it to everyt

In [24]:
with open("DB_multilingual_new_2.json", "w", encoding="utf-8") as f:
    json.dump(multilingual_data, f, ensure_ascii=False, indent=4)


TypeError: Object of type Series is not JSON serializable

In [ ]:
multilingual_data

[{'audioAddress': {'en': '', 'fa': ''},
  'repetitionText': {'en': '',
   'fa': 'من فرزند خداوندم*، کامل و شفا یافته و تمام، درخشنده در بازتاب عشق او*. در من آفرینش او تقدیس می\u200cشود و زندگی ابدی تضمین می\u200cگردد. در من عشق به کمال می\u200cرسد، ترس ناممکن می\u200cشود، و سرور بدون تضاد استقرار می\u200cیابد. من منزل مقدس خود خداوند هستم. من همان بهشت هستم که عشق او در آن ساکن است. من خود بی\u200cگناهی مقدس او هستم، زیرا در خلوص من خلوص خود او ساکن است.'},
  'title': {'en': '',
   'fa': 'من فرزند خداوند هستم، کامل و شفا یافته و تمام، درخشنده در بازتاب عشق او'},
  'text': {'en': "I am God's Son, complete and healed and whole, shining in the reflection of His Love. In me is His creation sanctified and guaranteed eternal life. In me is love perfected, fear impossible, and joy established without opposite. I am the holy home of God Himself. I am the Heaven where His Love resides. I am His holy Sinlessness Itself, for in my purity abides His Own.\n\nOur use for words is almost over now. Y

In [16]:
with open("DB_multilingual.json", "w", encoding="utf-8") as f:
    json.dump(multilingual_data, f, ensure_ascii=False, indent=4)

In [9]:
import pandas as pd
df = pd.read_csv("ACIM Alarm.csv")

In [13]:
df["repetition code"] = df["repetition code"].astype(str)

In [14]:
df["repetition code"]

0               2_times
1               2_times
2               2_times
3      3_times, 4_times
4      3_times, 4_times
             ...       
360          every_hour
361          every_hour
362          every_hour
363          every_hour
364          every_hour
Name: repetition code, Length: 365, dtype: object

In [15]:
import tqdm

for day_index, day_entries in enumerate(tqdm.tqdm(multilingual_data.values())):
    if(day_index == 0):
        continue
    day_entries[-1]["repetitionCode"] = df[df["day"] == day_index]["repetition code"].values[0].split(",")

100%|██████████| 366/366 [00:00<00:00, 6259.85it/s]


In [31]:
unique_repetition_codes = set()
for entries in db_multilingual.values():
    for entry in entries:
        codes = entry.get("repetitionCode", [])
        if isinstance(codes, list):
            unique_repetition_codes.update(codes)
        elif isinstance(codes, str):
            unique_repetition_codes.add(codes)

unique_repetition_codes = sorted(unique_repetition_codes)
print(unique_repetition_codes)

['1_time', '2_times', '3_times', '4_times', '5_times', '6_times', 'every_10_minutes', 'every_12_minutes', 'every_15_minutes', 'every_20_minutes', 'every_30_minutes', 'every_8_minutes', 'every_hour', 'nan']


In [32]:
unique_repetition_codes

['1_time',
 '2_times',
 '3_times',
 '4_times',
 '5_times',
 '6_times',
 'every_10_minutes',
 'every_12_minutes',
 'every_15_minutes',
 'every_20_minutes',
 'every_30_minutes',
 'every_8_minutes',
 'every_hour',
 'nan']

In [30]:
import json

with open("DB_multilingual.json", "r", encoding="utf-8") as f:
    db_multilingual = json.load(f)